In [4]:
# Library imports

import pandas as pd
import os
from qualitative_analysis import (
    clean_and_normalize,
    load_data,
    sanitize_dataframe
)
from qualitative_analysis.scenario_runner import run_scenarios
from qualitative_analysis.evaluation import (
    compute_kappa_metrics,
    run_alt_test_on_results,
    compute_classification_metrics_from_results
)
from qualitative_analysis.metrics.kappa import (
    compute_krippendorff_non_inferiority,
    print_non_inferiority_results
)


c:\Users\ocler\miniconda3\envs\gpt_rl\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Data loading

# Define data directory
data_dir = 'data/multiclass_user_case'
os.makedirs(data_dir, exist_ok=True)

# Define the path to your dataset
data_file_path = os.path.join(data_dir, 'student_gen_new_answers.xlsx')

# Load the data
data = load_data(data_file_path, file_type='xlsx', delimiter=';')

# Preview the data
data.head()

submission_date   id      exercise  \
0  12/06/2025 13:43  A01     Les ondes   
1  12/06/2025 13:46  A01         L'eau   
2  12/06/2025 13:48  A01     Le crayon   
3  12/06/2025 13:51  A01     Les lunes   
4  12/06/2025 13:52  A01  Les fossiles   

                          self_confidence accepted_suggested_prompt  \
0  Très confiant d'avoir la bonne réponse                       Oui   
1  Très confiant d'avoir la bonne réponse                       Oui   
2  Très confiant d'avoir la bonne réponse                       Oui   
3  Très confiant d'avoir la bonne réponse                       Oui   
4  Très confiant d'avoir la bonne réponse                       Oui   

                                       answer_1_eval answer_2_eval  \
0  donne les informations exactes pour répondre à...           NaN   
1  donne les informations exactes pour répondre à...           NaN   
2  donne les informations exactes pour répondre à...           NaN   
3  donne les informations exactes pour répondre à...           NaN   
4  donne les informations exactes pour répondre à...           NaN   

  answer_3_eval answer_4_eval answer_5_eval  ...  \
0           NaN           NaN           NaN  ...   
1           NaN           NaN           NaN  ...   
2           NaN           NaN           NaN  ...   
3           NaN           NaN           NaN  ...   
4           NaN           NaN           NaN  ...   

                                           Mots clés  \
0  Longueur d'onde & photorecepteurs ou cônes et ...   
1  Cycle hydrologique / Cycle de l'eau / Evaporta...   
2  Réfraction / changement & vitesse / lumière & ...   
3                Gibbeuse décroissante / pleine lune   
4  Trilobites & Balera / couche A & car c'est la ...   

                                             Process  \
0  La longueur d'onde : nous ne voyons qu'une pet...   
1                                                  -   
2  Lorsqu'un crayon est mis dans un verre d'eau, ...   
3                                                  -   
4                                                  -   

                                          Annotation Rater_Eliott  \
0  0: pas de mention des mots clés + pas d'explic...          2.0   
1  0: pas de mention des mots clés\n1: mention im...          0.0   
2  0: pas de mention des mots clés + pas d'explic...          1.0   
3  0: pas de mention des mots clés\n1: mention im...          1.0   
4  0: pas de mention des mots clés\n1: mention im...          1.0   

   Rater_chloe Rater_Oli Rater_Rania  \
0          2.0       1.0         1.0   
1          0.0       0.0         0.0   
2          2.0       1.0         1.0   
3          0.0       1.0         1.0   
4          0.0       0.0         0.0   

                                        Exemple faux  \
0  réponse : la propriété qui nous rend incable d...   
1  réponse : Le va-et-vient de l'eau est est un p...   
2  réponse : Quand un crayon est plongé dans l’ea...   
3  réponse : La lune a des phase différent suiven...   
4  réponse : les fossiles les plus anciens se tro...   

                                       Exemple moyen  \
0  réponse : La propriété physique qui rend certa...   
1  réponse : L’eau de la mer s’évapore grâce à la...   
2  réponse : Un crayon a l'air de changer de dire...   
3  réponse : Les phases de la lune évoluent en gé...   
4  réponse : Les plus anciens fossiles se trouven...   

                                       Exemple juste  
0  réponse : On ne peux pas voir le spectre car n...  
1  réponse : Ce phénomène ce nomme le cycle hydro...  
2  réponse : L'effet de déformation d'un crayon p...  
3  réponse : Dans une semaine on vera une pleine ...  
4  réponse : les fossile les plus ancien sont le ...  

[5 rows x 27 columns]

In [3]:
import os
import re
import unicodedata

# --- Normalization function ---
def normalize_name(nom):
    if pd.isna(nom):
        return ""
    name = str(nom).strip().lower()
    name = name.replace("'", " ").replace("-", " ")
    name = ''.join(
        c for c in unicodedata.normalize('NFD', name)
        if unicodedata.category(c) != 'Mn'
    )
    name = re.sub(r"\s+", "_", name)
    name = re.sub(r"[^a-z0-9_]", "", name)
    return name


# --- Normalize the name column in `data` ---
data['normalized_name'] = data['exercise'].apply(normalize_name)

# --- Load tasks_df from the same folder ---
tasks_file_path = os.path.join(data_dir, 'tasks_for_gpt4o_mini.xlsx')
tasks_df = pd.read_excel(tasks_file_path)

# --- Normalize 'Nom' column in tasks_df ---
tasks_df['normalized_name'] = tasks_df['Nom'].apply(normalize_name)

# --- Merge on normalized_name ---
data = data.merge(
    tasks_df[['normalized_name', 'CODE']],
    how='left',
    on='normalized_name'
)

# --- Rename the column for consistency ---
data.rename(columns={'CODE': 'code'}, inplace=True)

# --- Drop helper column if not needed ---
data.drop(columns=['normalized_name'], inplace=True)


In [4]:
# 1) Now define the new column names for cleaning
text_columns = ["réponse", "Type", "Mots clés", "Process", "Annotation", "Exemple faux", "Exemple moyen", "Exemple juste"]
integer_columns = ["code", "Rater_Oli", "Rater_chloe", "Rater_Eliott", "Rater_Rania"]

# 2) Clean and normalize the new columns
for col in text_columns:
    data[col] = clean_and_normalize(data[col])

# 4) Convert selected columns to integers, preserving NaNs
for col in integer_columns:
    data[col] = pd.to_numeric(data[col], errors="coerce").astype("Int64")  # Uses nullable integer type

# 5) Sanitize the DataFrame
data = sanitize_dataframe(data)

In [5]:
# Combine texts and entries

data['verbatim'] = data.apply(
    lambda row: (
        f"réponse: {row['réponse']}\n\n"
        f"type: {row['Type']}\n\n"
        f"mots_clés: {row['Mots clés']}\n\n"
        f"process: {row['Process']}\n\n"
        f"annotation: {row['Annotation']}\n\n"
        f"exemple_faux: {row['Exemple faux']}\n\n"
        f"exemple_moyen: {row['Exemple moyen']}\n\n"
        f"exemple_juste: {row['Exemple juste']}\n\n"
    ),
    axis=1
)

# Extract the list of verbatims
verbatims = data['verbatim'].tolist()

print(f"Total number of verbatims: {len(verbatims)}")
print(f"Verbatim example:\n{verbatims[0]}")

Total number of verbatims: 696
Verbatim example:
réponse: Lil humain ne voit quun petit bout des ondes de lumiere, entre 380 et 750 nanometres, quon appelle la lumiere visible. Cest parce que nos yeux ne sont sensibles qua ces longueurs donde-la. Du coup, les infrarouges et les ultraviolets existent, mais on ne les voit pas, car nos yeux ne sont pas faits pour ca.

type: Explication processus

mots_clés: Longueur d'onde & photorecepteurs ou cones et batonnets

process: La longueur d'onde : nous ne voyons qu'une petite partie du spectre lumineux parce que nos photorecepteurs sont specifiquement regles pour cette gamme de longueurs d'onde.

annotation: 0: pas de mention des mots cles + pas d'explication correcte du processus 1: manque de clarete sur les mots cles ou l'explication du phenomeme ou rajout de details hors sujets dans les mots cles ou l'explication 2: mention claire, suffisante et ciblee sur le but precis de l'exercice concernant les mots cles et l'explication du phenomene

e

In [20]:
scenarios = [
    {
        "provider_llm1": "azure",
        "model_name_llm1": "gpt-4o",
        "temperature_llm1": 0,

        # For the "improver" LLM2
        "provider_llm2": "azure",
        "model_name_llm2": "gpt-4o",
        "temperature_llm2": 0.7,

        "max_iterations": 1,
        "n_completions": 1,
        "prompt_name": "eval_rep",
        
        # Data configuration
        "subsample_size": -1,  # Size of data subset to use
        "use_validation_set": False,  # Whether to use a validation set
        "validation_size": 10,  # Size of validation set (if used)
        "random_state": 42,  # Random state for reproducibility

        # Our initial prompt
        "template": """
Vous êtes un assistant chargé d’évaluer des entrées de données.

Les données comprennent les colonnes suivantes :
- "réponse": La réponse à évaluer
- "type": Le type de réponse attendue
- "mots-clés": Les mots-clés attendus. Tous les mot-clés ne doivent pas nécessairement être présents dans la réponse.
- "process": L'explication du processus, si celui-ci est attendu.
- "annotation": La grille d'annotation pour cette tâche.
- "exemple_faux": Un exemple de réponse fausse (0)
- "exemple_moyen": Un exemple de réponse partiellement correcte (1)
- "exemple_juste": Un exemple de réponse correcte (2)

Voici une entrée à évaluer :
{verbatim_text}

Tâche d’évaluation :
Pour chaque entrée, évaluer si la réponse est fausse, partiellement correcte ou correcte, en utilisant l’échelle fournie (annotation).
Répondre en donnant le Raisonnement et la Classification (0, 1 ou 2) de la réponse.
""",
        "prefix": "Classification",
        "json_output": True,
        "selected_fields": ["Classification"],
        "label_type": "int",
        "response_template":
        """
S'il te plait, suis le format JSON ci-dessous :
```json
{{
  "Raisonnement": "Ton raisonnement ici",
  "Classification": "Ton integer ici"
}}
""",
    },
        {
        "provider_llm1": "azure",
        "model_name_llm1": "gpt-4o",
        "temperature_llm1": 0,

        # For the "improver" LLM2
        "provider_llm2": "azure",
        "model_name_llm2": "gpt-4o",
        "temperature_llm2": 0.7,

        "max_iterations": 1,
        "n_completions": 1,
        "prompt_name": "kind",
        
        # Data configuration
        "subsample_size": -1,  # Size of data subset to use
        "use_validation_set": False,  # Whether to use a validation set
        "validation_size": 10,  # Size of validation set (if used)
        "random_state": 42,  # Random state for reproducibility

        # Our initial prompt
        "template": """
Vous êtes un assistant chargé d’évaluer des entrées de données.

Les données comprennent les colonnes suivantes :
- "réponse": La réponse à évaluer
- "type": Le type de réponse attendue
- "mots-clés": Les mots-clés attendus. Tous les mot-clés ne doivent pas nécessairement être présents dans la réponse.
- "process": L'explication du processus, si celui-ci est attendu.
- "annotation": La grille d'annotation pour cette tâche.
- "exemple_faux": Un exemple de réponse fausse (0)
- "exemple_moyen": Un exemple de réponse partiellement correcte (1)
- "exemple_juste": Un exemple de réponse correcte (2)

Voici une entrée à évaluer :
{verbatim_text}

Tâche d’évaluation :
Pour chaque entrée, évaluer si la réponse est fausse, partiellement correcte ou correcte, en utilisant l’échelle fournie (annotation).
La réponse est écrite par des enfants, l'orthographe et la grammaire ne sont pas importantes.
La réponse n'a pas besoin d'être parfaitement similaire à l'exemple juste pour être considérée comme un 2. Si la réponse est correcte dans l'esprit, elle peut être considérée comme un 2 plutôt que comme un 1.
Répondre en donnant le Raisonnement et la Classification (0, 1 ou 2) de la réponse.
""",
        "prefix": "Classification",
        "json_output": True,
        "selected_fields": ["Classification"],
        "label_type": "int",
        "response_template":
        """
S'il te plait, suis le format JSON ci-dessous :
```json
{{
  "Raisonnement": "Ton raisonnement ici",
  "Classification": "Ton integer ici"
}}
""",
    },
]

In [21]:
# 9) Run scenarios and get results

annotation_columns = ['Rater_Oli', 'Rater_chloe', 'Rater_Eliott', 'Rater_Rania']
labels = [0,1,2]

# Filter labeled data (drop rows with NaN in any annotation column)
labeled_data = data.dropna(subset=annotation_columns)
unlabeled_data = data[~data.index.isin(labeled_data.index)]

n_runs = 3  # Number of runs per scenario
verbose = True  # Whether to print verbose output

# Run the scenarios - this only runs the LLM and saves all the generated labels
annotated_results_llm = run_scenarios(
    scenarios=scenarios,
    data=labeled_data,
    annotation_columns=annotation_columns,
    labels=labels,
    n_runs=n_runs,
    verbose=verbose
)

Using all labeled data: 70 samples
Scenario 'eval_rep' - Train size (all data): 70, No validation set

=== Processing Verbatim 1/70 ===
Prompt:

Vous êtes un assistant chargé d’évaluer des entrées de données.

Les données comprennent les colonnes suivantes :
- "réponse": La réponse à évaluer
- "type": Le type de réponse attendue
- "mots-clés": Les mots-clés attendus. Tous les mot-clés ne doivent pas nécessairement être présents dans la réponse.
- "process": L'explication du processus, si celui-ci est attendu.
- "annotation": La grille d'annotation pour cette tâche.
- "exemple_faux": Un exemple de réponse fausse (0)
- "exemple_moyen": Un exemple de réponse partiellement correcte (1)
- "exemple_juste": Un exemple de réponse correcte (2)

Voici une entrée à évaluer :
réponse: Lil humain ne voit quun petit bout des ondes de lumiere, entre 380 et 750 nanometres, quon appelle la lumiere visible. Cest parce que nos yeux ne sont sensibles qua ces longueurs donde-la. Du coup, les infrarouges et

In [ ]:
# Save the annotated results to a CSV file
annotated_results_llm.to_csv("data/multiclass_user_case/outputs/annotated_results_students__.csv", sep=";", index=False, encoding="utf-8-sig")

In [ ]:
# Optionally, load the annotated results from a CSV file if needed

annotated_results_llm = pd.read_csv(
    "data/outputs/annotated_results_students.csv",
    sep=";",
    encoding="utf-8-sig"
)

In [17]:
# 10) Compute metrics from the detailed results
# First, compute kappa metrics

epsilon = 0.2  # Epsilon parameter for ALT test
annotation_columns = ['Rater_Oli', 'Rater_chloe', 'Rater_Eliott', 'Rater_Rania']
labels = [0,1,2]
verbose = True

kappa_df, detailed_kappa_metrics = compute_kappa_metrics(
    detailed_results_df=annotated_results_llm,
    annotation_columns=annotation_columns,
    labels=labels,
    kappa_weights='linear'
)

print("\n=== Detailed Kappa Metrics ===")
if detailed_kappa_metrics:
    for scenario_key, metrics in detailed_kappa_metrics.items():
        print(f"\nScenario: {scenario_key}")
        
        print("\nLLM vs Human Annotators:")
        print(metrics['llm_vs_human_df'])
        
        print("\nHuman vs Human Annotators:")
        print(metrics['human_vs_human_df'])
else:
    print("No detailed kappa metrics available.")


=== Columns in detailed_results_df (in compute_kappa_metrics) ===
['sample_id', 'split', 'verbatim', 'iteration', 'Rater_Oli', 'Rater_chloe', 'Rater_Eliott', 'Rater_Rania', 'ModelPrediction', 'Raisonnement', 'run', 'prompt_name', 'use_validation_set']

=== Detailed Kappa Metrics ===

Scenario: eval_rep_iteration_1

LLM vs Human Annotators:
  Human_Annotator  Cohens_Kappa
0       Rater_Oli      0.643895
1     Rater_chloe      0.557783
2    Rater_Eliott      0.599542
3     Rater_Rania      0.612397

Human vs Human Annotators:
    Annotator_1   Annotator_2  Cohens_Kappa
0     Rater_Oli   Rater_chloe      0.778157
1     Rater_Oli  Rater_Eliott      0.633333
2     Rater_Oli   Rater_Rania      0.747960
3   Rater_chloe  Rater_Eliott      0.533119
4   Rater_chloe   Rater_Rania      0.740981
5  Rater_Eliott   Rater_Rania      0.537796

Scenario: kind_iteration_1

LLM vs Human Annotators:
  Human_Annotator  Cohens_Kappa
0       Rater_Oli      0.771242
1     Rater_chloe      0.675615
2    Rater_

In [ ]:
# Run the non-inferiority test
non_inferiority_results = compute_krippendorff_non_inferiority(
    detailed_results_df=annotated_results_llm,
    annotation_columns=annotation_columns,
    model_column="ModelPrediction",
    level_of_measurement='ordinal',
    non_inferiority_margin=-0.05,
    n_bootstrap=2000, 
    confidence_level=90.0,
    random_seed=42, 
    verbose=False   
)

# Print results in a formatted way
print_non_inferiority_results(non_inferiority_results, show_per_run=False)


=== Non-inferiority Test: eval_rep_iteration_1 ===
Human trios α: 0.7395 ± 0.0000
Model trios α: 0.7197 ± 0.0108
Δ = model − human = -0.0197 ± 0.0108
90% CI: [-0.0648, 0.0229]
Non-inferiority demonstrated in 0/3 runs
❌ Non-inferiority NOT demonstrated in any run (margin = -0.05)

=== Non-inferiority Test: kind_iteration_1 ===
Human trios α: 0.7395 ± 0.0000
Model trios α: 0.7517 ± 0.0011
Δ = model − human = +0.0122 ± 0.0011
90% CI: [-0.0263, 0.0483]
Non-inferiority demonstrated in 3/3 runs
✅ Non-inferiority consistently demonstrated across all runs (margin = -0.05)


In [36]:
epsilon = 0.2
# Then, run ALT test
alt_test_df = run_alt_test_on_results(
    detailed_results_df=annotated_results_llm,
    annotation_columns=annotation_columns,
    labels=labels,
    epsilon=epsilon,
    alpha=0.05,
    verbose=verbose
)
alt_test_df = alt_test_df.drop(
    columns=["iteration", "run", "use_validation_set", "N_val", "n_runs"]
)

pd.set_option("display.max_colwidth", None)   # show full content in each cell
alt_test_df.tail(2)


=== Columns in detailed_results_df (in run_alt_test_on_results) ===
['sample_id', 'split', 'verbatim', 'iteration', 'Rater_Oli', 'Rater_chloe', 'Rater_Eliott', 'Rater_Rania', 'ModelPrediction', 'Raisonnement', 'run', 'prompt_name', 'use_validation_set']
=== ALT Test: Label Debugging ===
Label counts for each rater:
  ModelPrediction: 70 valid labels
  Rater_Oli: 70 valid labels
  Rater_chloe: 70 valid labels
  Rater_Eliott: 70 valid labels
  Rater_Rania: 70 valid labels

Label types for each rater:
  ModelPrediction: int64
  Rater_Oli: int64
  Rater_chloe: int64
  Rater_Eliott: int64
  Rater_Rania: int64

Mixed types across raters: False

=== Converting labels to consistent types ===
Using label_type: int
Model predictions type after conversion: <class 'numpy.int32'>
Rater_Oli type after conversion: <class 'numpy.int32'>
Rater_chloe type after conversion: <class 'numpy.int32'>
Rater_Eliott type after conversion: <class 'numpy.int32'>
Rater_Rania type after conversion: <class 'numpy.in

prompt_name  N_train  winning_rate_train  passed_alt_test_train  \
6    eval_rep      210                0.25                  False   
7        kind      210                1.00                   True   

   avg_adv_prob_train  \
6            0.820238   
7            0.894048   

                                                                                 p_values_train  
6      [0.22107870937654348, 0.030437511386181657, 0.0005202099158283915, 0.027930631575721534]  
7  [0.003918048763420232, 0.0001494782332300548, 6.144338877703003e-07, 0.00036692474298443507]

In [37]:
alt_test_df

prompt_name  N_train  winning_rate_train  passed_alt_test_train  \
0    eval_rep       70                0.25                  False   
1    eval_rep       70                0.25                  False   
2    eval_rep       70                0.75                   True   
3        kind       70                1.00                   True   
4        kind       70                1.00                   True   
5        kind       70                1.00                   True   
6    eval_rep      210                0.25                  False   
7        kind      210                1.00                   True   

   avg_adv_prob_train  \
0            0.835714   
1            0.792857   
2            0.832143   
3            0.892857   
4            0.892857   
5            0.896429   
6            0.820238   
7            0.894048   

                                                                                  p_values_train  
0        [0.1082742968063706, 0.018464116750660134, 4.638738892638575e-05, 0.021123853341323526]  
1        [0.40406004597658246, 0.060109598727739424, 0.0013747402872524277, 0.05288873457213529]  
2      [0.15090178534667734, 0.012738818680145406, 0.00013950207130636092, 0.009779306813705787]  
3  [0.003918048763420232, 0.00018198848557176125, 7.877062064912272e-07, 0.00028472232125581503]  
4    [0.003918048763420232, 8.445772854664187e-05, 7.877062064912272e-07, 0.0005313295864416753]  
5  [0.003918048763420232, 0.00018198848557176125, 2.678892503284466e-07, 0.00028472232125581503]  
6       [0.22107870937654348, 0.030437511386181657, 0.0005202099158283915, 0.027930631575721534]  
7   [0.003918048763420232, 0.0001494782332300548, 6.144338877703003e-07, 0.00036692474298443507]

In [24]:
# Finally, compute classification metrics
classification_df = compute_classification_metrics_from_results(
    detailed_results_df=annotated_results_llm,
    annotation_columns=annotation_columns,
    labels=labels
)

pd.set_option("display.max_columns", None)    # show all columns
classification_df


=== Columns in detailed_results_df (in compute_classification_metrics_from_results) ===
['sample_id', 'split', 'verbatim', 'iteration', 'Rater_Oli', 'Rater_chloe', 'Rater_Eliott', 'Rater_Rania', 'ModelPrediction', 'Raisonnement', 'run', 'prompt_name', 'use_validation_set']


prompt_name  iteration  n_runs  use_validation_set  N_train  N_val  \
0    eval_rep          1       3               False      210      0   
1        kind          1       3               False      210      0   

   global_accuracy_train  global_recall_train  global_error_rate_train  \
0               0.733333             0.718519                 0.266667   
1               0.828571             0.833333                 0.171429   

   class_0_recall_train  class_0_error_rate_train  \
0              0.883333                  0.116667   
1              0.866667                  0.133333   

   class_0_correct_count_train  class_0_missed_count_train  \
0                           53                           7   
1                           52                           8   

   class_0_false_positives_train  class_1_recall_train  \
0                              6              0.822222   
1                              5              0.800000   

   class_1_error_rate_train  class_1_correct_count_train  \
0                  0.177778                           74   
1                  0.200000                           72   

   class_1_missed_count_train  class_1_false_positives_train  \
0                          16                             40   
1                          18                             15   

   class_2_recall_train  class_2_error_rate_train  \
0              0.450000                  0.550000   
1              0.833333                  0.166667   

   class_2_correct_count_train  class_2_missed_count_train  \
0                           27                          33   
1                           50                          10   

   class_2_false_positives_train  
0                             10  
1                             16

In [35]:
verbose = True
labels = [0,1,2]
annotation_columns = []
epsilon = 0.2
n_runs = 1  

scenarios = [
    {
        "provider_llm1": "azure",
        "model_name_llm1": "gpt-4o",
        "temperature_llm1": 0,

        # For the "improver" LLM2
        "provider_llm2": "azure",
        "model_name_llm2": "gpt-4o",
        "temperature_llm2": 0.7,

        "max_iterations": 1,
        "n_completions": 1,
        "prompt_name": "French",
        
        # Data configuration
        "subsample_size": -1,  # Size of data subset to use
        "use_validation_set": False,  # Whether to use a validation set
        "validation_size": 10,  # Size of validation set (if used)
        "random_state": 42,  # Random state for reproducibility

        # Our initial prompt
        "template": """
Vous êtes un assistant chargé d’évaluer des entrées de données.

Les données comprennent les colonnes suivantes :
- "réponse": La réponse à évaluer
- "type": Le type de réponse attendue
- "mots-clés": Les mots-clés attendus. Tous les mot-clés ne doivent pas nécessairement être présents dans la réponse.
- "process": L'explication du processus, si celui-ci est attendu.
- "annotation": La grille d'annotation pour cette tâche.
- "exemple_faux": Un exemple de réponse fausse (0)
- "exemple_moyen": Un exemple de réponse partiellement correcte (1)
- "exemple_juste": Un exemple de réponse correcte (2)

Voici une entrée à évaluer :
{verbatim_text}

Tâche d’évaluation :
Pour chaque entrée, évaluer si la réponse est fausse, partiellement correcte ou correcte, en utilisant l’échelle fournie (annotation).
La réponse est écrite par des enfants, l'orthographe et la grammaire ne sont pas importantes.
La réponse n'a pas besoin d'être parfaitement similaire à l'exemple juste pour être considérée comme un 2. Si la réponse est correcte dans l'esprit, elle peut être considérée comme un 2 plutôt que comme un 1.
Répondre en donnant le Raisonnement et la Classification (0, 1 ou 2) de la réponse.
""",
        "prefix": "Classification",
        "json_output": True,
        "selected_fields": ["Classification"],
        "label_type": "int",
        "response_template":
        """
S'il te plait, suis le format JSON ci-dessous :
```json
{{
  "Raisonnement": "Ton raisonnement ici",
  "Classification": "Ton integer ici"
}}
""",
    },
]

# Run the scenarios - this only runs the LLM and saves all the generated labels
full_results_llm = run_scenarios(
    scenarios=scenarios,
    data=data,
    annotation_columns=annotation_columns,
    labels=labels,
    n_runs=n_runs,
    verbose=verbose
)

Using all labeled data: 696 samples
Scenario 'French' - Train size (all data): 696, No validation set

=== Processing Verbatim 1/696 ===
Prompt:

Vous êtes un assistant chargé d’évaluer des entrées de données.

Les données comprennent les colonnes suivantes :
- "réponse": La réponse à évaluer
- "type": Le type de réponse attendue
- "mots-clés": Les mots-clés attendus. Tous les mot-clés ne doivent pas nécessairement être présents dans la réponse.
- "process": L'explication du processus, si celui-ci est attendu.
- "annotation": La grille d'annotation pour cette tâche.
- "exemple_faux": Un exemple de réponse fausse (0)
- "exemple_moyen": Un exemple de réponse partiellement correcte (1)
- "exemple_juste": Un exemple de réponse correcte (2)

Voici une entrée à évaluer :
réponse: Lil humain ne voit quun petit bout des ondes de lumiere, entre 380 et 750 nanometres, quon appelle la lumiere visible. Cest parce que nos yeux ne sont sensibles qua ces longueurs donde-la. Du coup, les infrarouges e

In [37]:
# turn the index of `data` into a column that matches full_results_llm
data_pos = (
    data
      .reset_index()                      # old index → new column "index"
      .rename(columns={"index": "sample_id"})
)

# keep only the columns you actually want from the LLM results
llm_subset = full_results_llm[["sample_id", "ModelPrediction", "Raisonnement"]]

# one-to-one merge; pandas will raise if the assumption is broken
full_merged_results_llm = data_pos.merge(
            llm_subset,
            on="sample_id",
            how="left",
            validate="one_to_one"         # guarantees no duplicates creep in
         )

# put sample_id back as the index so the shape matches the original
full_merged_results_llm = full_merged_results_llm.set_index("sample_id")

In [38]:
full_merged_results_llm.to_csv("data/outputs/full_results_student_gen.csv", sep=";", index=False, encoding="utf-8-sig")